# Trajectory Compression

**Context**: When the number of geolocation datapoints get too large (typically 50,000 datapoints), data visualisation becomes a challenge. To overcome this challenge, we look at ways to select a meaningful set of points to plot from a given trajectory.

**Literature Review**

Many trajectory compression algorithms implemented in C++ can be found in: https://github.com/uestc-db/traj-compression

The authors of the above repository wrote a paper titled "Trajectory Simplification: An Experimental Study and Quality Analysis" about their evaluation.

Link to the paper: http://www.vldb.org/pvldb/vol11/p934-zhang.pdf

**To-do list**
- Implement the algorithms found in https://github.com/uestc-db/traj-compression in Python.
- Evaluate the algorithms using the metrics proposed by the paper.
- Visualise them and see if they make sense.

In [71]:
import pandas as pd
import numpy as np
from math import radians, cos, sin, asin, sqrt, atan, pi
import os

import folium
from folium import plugins

**Metrics** to determine (numerically) the quality of trajectory compression, they include:
- Perpendicular Euclidean Distance (PED)
- Synchronous Euclidean Distance (SED)
- Direction Aware Distance (DAD)

In [1]:
def dist(point1, point2):
    '''
    :param point1: an object with attributes `lat` and `lon`
    :param point2: an object with attributes `lat` and `lon`
    '''
    return sqrt((point1.lat - point2.lat))

def ped(anc_point1, anc_point2, point3):
    '''
    :param anc_point1: an object with attributes `lat`, `lon`, `time`, represents anchor point
    :param anc_point2: an object with attributes `lat`, `lon`, `time`, represents anchor point
    :param point3: an object with attributes `lat`, `lon`, `time`, represents a point estimated from 
        `anc_point1` and `anc_point2`
    
    Assumptions: anc_point1.time <= anc_point2.time
    '''
    
    if (point1.lat == point2.lat) and (point1.lon == point2.lon):
        return dist(point1, point3)
    else:
        pass
    
def sed()

Some auxiliary functions to support threshold algorithm

In [72]:
def haversine(lon1, lat1, lon2, lat2):
    """
    Calculate the great circle distance (in metres) between two points on the earth (specified in decimal degrees)
    
    :param lon1: longitude of point 1
    :param lat1: longitude of point 1
    :param lon2: longitude of point 2
    :param lat2: longitude of point 2
    :return: the distance between (lon1, lat1) and (lon2, lat2), in metres
    """
    # convert decimal degrees to radians 
    lon1, lat1, lon2, lat2 = map(radians, [lon1, lat1, lon2, lat2])

    # haversine formula 
    dlon = lon2 - lon1 
    dlat = lat2 - lat1 
    a = sin(dlat/2)**2 + cos(lat1) * cos(lat2) * sin(dlon/2)**2
    c = 2 * asin(sqrt(a)) 
    r = 6378.1 # Radius of earth in kilometers. Use 3956 for miles
    return c * r * 1000

def calc_angle(point_a, point_b):
    dlon = point_b.lon - point_a.lon
    dlat = point_b.lat - point_a.lat
    
    if dlat != 0:
        return atan(dlon/dlat)
    else:
        return pi / 2
    
def calc_speed(a, b):
    return haversine(a.lon, a.lat, b.lon, b.lat) / abs((a.time - b.time).total_seconds())

def safe_speed(sample_b, sample_c, point_c, point_d, point_e,
               speed_threshold):
    '''
    test
    '''
    sample_speed = calc_speed(sample_b, sample_c)
    trajectory_speed = calc_speed(point_c, point_d)
    de_speed = calc_speed(point_d,point_e)
    
    if abs(sample_speed - de_speed) > speed_threshold or abs(trajectory_speed - de_speed) > speed_threshold:
        return False
    else:
        return True
    
def safe_orientation(sample_b, sample_c, point_c, point_d, point_e,
                     ori_threshold):
    '''
    test
    '''
    angle_sample_bc = calc_angle(sample_b, sample_c)
    angle_de = calc_angle(point_d, point_e)
    angle_sample_bc_de = angle_de - angle_sample_bc
    angle_trajectory_cd = calc_angle(point_c, point_d)
    angle_trajectory_cd_de = angle_de - angle_trajectory_cd

    if (abs(angle_sample_bc_de) > ori_threshold) or (abs(angle_trajectory_cd_de) > ori_threshold):
        return False
    else:
        return True

In [23]:
def threshold(df, speedThres=25, directionThres=0.8):
    '''
    :param df: dataframe containing variables `lat`, `lon` and `time`
    :param speedThres: the threshold for speed in metres per second
    :param directionThres: the threshold for change in orientation in radians
    :return: dataframe containing variables `lat`, `lon` and `time`, representing a compressed trajectory
    '''
    sampledPoints = pd.DataFrame(columns=list(df.columns))
    
    sampledPoints.loc[0, :] = df.loc[0,:]
    sampledPoints.loc[1, :] = df.loc[1,:]
    
    for i in range(2, len(df)):
        samp_size = len(sampledPoints)
        if (safe_speed(sampledPoints.loc[samp_size-2,:], sampledPoints.loc[samp_size-1,:], 
                       df.loc[i-2,:], df.loc[i-1,:], df.loc[i,:],
                       speedThres) and\
            safe_orientation(sampledPoints.loc[samp_size-2,:], sampledPoints.loc[samp_size-1,:], 
                             df.loc[i-2,:], df.loc[i-1,:], df.loc[i,:],
                             directionThres)):
            continue
        else:
            sampledPoints.loc[len(sampledPoints), :] = df.loc[i,:]
    
    return sampledPoints

In [17]:
def thresholdOriginal(speedThres, directionThres):
    '''
    :param speedThres: 
    :param directionThres: 
    '''
    def isInRing(center, smallRadius, largeRadius, point):
        '''
        :return True: if the point `point` falls within the ring formed by 2 concentric circles with center `center` 
            and radii `smallRadius` and `largeRadius`
        :return False:
        '''
        temp = (point[0]-center[0])**2 + (point[1]-center[1])**2
        if  smallRadius**2 <= temp and temp <= largeRadius**2:
            return True
        else:
            return False
    def isInSector(center, slope1, slope2, point):
        
        return True
    
        return False
    
    def isInSafeArea(nextPoint, previousPoints):
        
        return True
        
        return False

**Import a trajectory from GeoLife dataset**

In [18]:
# GEOLIFE_DATA_PATH = r"C:\Users\Tay\Documents\GitHub\Trajectory-Data-Mining\Geolife Trajectories 1.3\Data"
GEOLIFE_DATA_PATH = r"C:\Users\tay.yq.XTRAMAN\Documents\GitHub\Trajectory-Data-Mining\Geolife Trajectories 1.3\Data"

In [19]:
users = os.listdir(GEOLIFE_DATA_PATH)
print("Number of users in Geolife dataset: " + str(len(users)))

Number of users in Geolife dataset: 182


In [7]:
def readUserTraj(path_to_user):
    '''
    :param path_to_user: a path to the user's dataset according to the Geolife dataset file system
    :return: a dataframe containing all of the user's trajectories. 
    Note that a person can have more than 1 disconnected trajectory.
    '''
    trajs = os.listdir(path_to_user + r"\Trajectory")
    col_names = ["lat", "lon", "alt", "date", "time"]
    userTraj = pd.DataFrame(columns=["lat", "lon", "alt", "time"])
    
    for i in range(len(trajs)):
        TRAJ_PATH = path_to_user + r"\Trajectory" + r"\\" + trajs[i]
        traj = pd.read_csv(TRAJ_PATH, skiprows=6, header=None, usecols=[0,1,3,5,6], names=col_names)

        # to combine date and time and change it to `datetime` type
        for i in range(len(traj)):
            traj.loc[i, "time"] = pd.to_datetime(traj.loc[i, "date"] + " " + traj.loc[i, "time"])

        traj = traj.drop(columns="date")
        userTraj = userTraj.append(traj)
    
    userTraj = userTraj.reset_index(drop=True)
    
    return userTraj

In [8]:
%%time
trajDataFrame = readUserTraj(GEOLIFE_DATA_PATH + r"\\" + users[1])

Wall time: 50.7 s


In [9]:
trajDataFrame.head()

lat         lon  alt                 time
0  39.984094  116.319236  492  2008-10-23 05:53:05
1  39.984198  116.319322  492  2008-10-23 05:53:06
2  39.984224  116.319402  492  2008-10-23 05:53:11
3  39.984211  116.319389  492  2008-10-23 05:53:16
4  39.984217  116.319422  491  2008-10-23 05:53:21

**Compressing the trajectory data**

In [73]:
%%time
compressedTraj = threshold(trajDataFrame[:10000])

Wall time: 19.6 s


In [74]:
compressedTraj

lat      lon  alt                 time
0     39.9841  116.319  492  2008-10-23 05:53:05
1     39.9842  116.319  492  2008-10-23 05:53:06
2     39.9847   116.32  320  2008-10-23 05:53:23
3     39.9847   116.32  325  2008-10-23 05:53:28
4     39.9846   116.32  324  2008-10-23 05:53:43
...       ...      ...  ...                  ...
3306  39.9981  116.309  133  2008-10-25 11:10:35
3307  40.0042   116.31  120  2008-10-25 11:12:00
3308  40.0044   116.31  118  2008-10-25 11:12:03
3309  40.0059  116.313  122  2008-10-25 11:12:36
3310   40.006  116.313  122  2008-10-25 11:12:37

[3311 rows x 4 columns]

The dataset of size 108,607 is too large for visualisation. Note that the data is very dense, geolocation records are only 5 seconds apart.

In [63]:
def dfToJSON(traj, color="black", icon="circle"):
    '''
    :param traj: a dataframe with variables `lat`, `lon`, `time`
    :return features: a TimeStampedGeoJSON object that suits plotting Folium animations
    '''
    
    features = []
    
    for i in range(len(traj)):
        feature = {
            "type": "Feature",
            "geometry": {
                "type": "Point",
                'coordinates': [traj.lon[i], traj.lat[i]]
            },
            "properties": {
                "time": str(traj.time[i]),
                "icon": icon,
                "style": {"color": color, "radius": 0.01}
            }
        }
        features.append(feature)
    
    return features

def plot(traj, compressedTraj, zoom_start=10, period='PT1M'):
    '''
    :param traj: a dataframe with variables `lat`, `lon` and `time`
    :param compressedTraj: a dataframe with variables `lat`, `lon` and `time`
    :return: None
    will plot and animate the trajectory and its compressed version using Folium
    '''
    m = folium.Map(location=[traj.lat[0], traj.lon[0]], zoom_start=zoom_start)
    
    features = dfToJSON(traj, color="black")
    temp = dfToJSON(compressedTraj, color="red")
    
    for feature in temp:
        features.append(feature)
    
    # add points from traj
    plugins.TimestampedGeoJson({
        'type': 'FeatureCollection',
        'features': features,
    }, period=period, add_last_point=False, loop=False, auto_play = False).add_to(m)
    
    # adds a fullscreen button at the 'topright' corner of the plot
    plugins.Fullscreen(position='topright').add_to(m)
    
    return m

In [75]:
plot(trajDataFrame[:10000], compressedTraj, zoom_start=12, period='PT1H')

In [78]:
plot(trajDataFrame[:1], compressedTraj, zoom_start=12, period='PT1H')